In [3]:
print(spark.version)


3.4.1


In [1]:
import os

# Charger le jar kafka dans un notebook (obligatoire)
os.environ["PYSPARK_SUBMIT_ARGS"] = "--packages org.apache.spark:spark-sql-kafka-0-10_2.12:3.4.1 pyspark-shell"


In [ ]:
from kafka import KafkaConsumer
import json

# Config consumer Kafka
consumer = KafkaConsumer(
    'accidents_topic_v3',
    bootstrap_servers='localhost:9092',
    auto_offset_reset='earliest',  # lire depuis le début du topic
    enable_auto_commit=True,
    value_deserializer=lambda x: json.loads(x.decode('utf-8'))
)

print("Consumer Kafka démarré, affichage des messages reçus...")

for message in consumer:
    print(message.value)


Consumer Kafka démarré, affichage des messages reçus...
{'features': [-5.85, -18.38, 53.89, 30.95, 13.92, 24.44, 4.57, 33.63, 9757.0, 9890.0, 7711.0, 11.0, 15.0, 2.0]}
{'features': [24.66, 11.05, 76.83, 30.47, 0.71, 20.42, 3.95, 48.2, 7285.0, 5227.0, 7278.0, 3.0, 7.0, 1.0]}
{'features': [33.01, 15.41, 71.43, 28.09, 9.64, 24.47, 1.9, 39.58, 4108.0, 1748.0, 6566.0, 16.0, 6.0, 2.0]}
{'features': [-0.14, 7.81, 45.75, 31.12, 9.52, 36.63, 3.67, 50.18, 7137.0, 4800.0, 7865.0, 10.0, 8.0, 2.0]}
{'features': [14.67, -1.73, 25.66, 30.93, 9.45, 21.98, 2.73, 95.51, 7625.0, 8243.0, 958.0, 3.0, 8.0, 2.0]}
{'features': [38.48, 9.47, 71.45, 30.29, 9.67, 29.9, 1.0, 61.09, 8996.0, 5927.0, 4966.0, 2.0, 11.0, 1.0]}
{'features': [38.43, 14.36, 71.18, 31.99, 12.09, 20.68, 1.77, 80.34, 233.0, 3009.0, 3300.0, 18.0, 7.0, 2.0]}
{'features': [13.53, 7.99, 85.75, 29.43, 4.6, 13.58, 1.58, 72.26, 2999.0, 8926.0, 6051.0, 8.0, 15.0, 0.0]}
{'features': [7.14, 3.61, 42.64, 31.06, 1.07, 38.83, 0.26, 54.38, 986.0, 10661.0

In [ ]:
from kafka import KafkaConsumer
import json
from pyspark.sql import SparkSession
from pyspark.ml.linalg import Vectors
from pyspark.ml.classification import DecisionTreeClassificationModel
from pyspark.sql import Row

# 1. Créer la Spark session
spark = SparkSession.builder.appName("KafkaConsumerDT").getOrCreate()

# 2. Charger ton modèle
model_path = "models/le_model_dt"
dt_model = DecisionTreeClassificationModel.load(model_path)

# 3. Configurer Kafka Consumer
consumer = KafkaConsumer(
    'accidents_topic_v3',
    bootstrap_servers='localhost:9092',
    auto_offset_reset='earliest',
    enable_auto_commit=True,
    value_deserializer=lambda x: json.loads(x.decode('utf-8'))
)

print("Consumer Kafka démarré, attente des messages...")

# 4. Traiter message par message
for message in consumer:
    try:
        features_list = message.value.get("features")
        if not features_list:
            print("Message ignoré, pas de 'features'.")
            continue
        
        # Affiche les features reçues
        print("Features reçues :", features_list)

        # Convertir en vecteur Spark ML
        features_vector = Vectors.dense(features_list)

        # Créer DataFrame Spark pour la prédiction
        df = spark.createDataFrame([Row(features=features_vector)])

        # Faire la prédiction
        prediction_df = dt_model.transform(df)
        prediction = prediction_df.collect()[0]['prediction']

        # Afficher la prédiction
        print(f"Prediction: {prediction}\n")  # Le \n pour bien séparer les lignes

    except Exception as e:
        print(f"Erreur lors du traitement du message: {e}")


25/07/08 07:44:27 WARN Utils: Your hostname, DESKTOP-DD5N9SQ resolves to a loopback address: 127.0.1.1; using 172.30.167.134 instead (on interface eth0)
25/07/08 07:44:27 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/07/08 07:44:49 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
                                                                                

Consumer Kafka démarré, attente des messages...
Features reçues : [-5.85, -18.38, 53.89, 30.95, 13.92, 24.44, 4.57, 33.63, 9757.0, 9890.0, 7711.0, 11.0, 15.0, 2.0]


Prediction: 2.0

Features reçues : [24.66, 11.05, 76.83, 30.47, 0.71, 20.42, 3.95, 48.2, 7285.0, 5227.0, 7278.0, 3.0, 7.0, 1.0]


Prediction: 2.0

Features reçues : [33.01, 15.41, 71.43, 28.09, 9.64, 24.47, 1.9, 39.58, 4108.0, 1748.0, 6566.0, 16.0, 6.0, 2.0]
Prediction: 3.0

Features reçues : [-0.14, 7.81, 45.75, 31.12, 9.52, 36.63, 3.67, 50.18, 7137.0, 4800.0, 7865.0, 10.0, 8.0, 2.0]


Prediction: 2.0

Features reçues : [14.67, -1.73, 25.66, 30.93, 9.45, 21.98, 2.73, 95.51, 7625.0, 8243.0, 958.0, 3.0, 8.0, 2.0]
Prediction: 2.0

Features reçues : [38.48, 9.47, 71.45, 30.29, 9.67, 29.9, 1.0, 61.09, 8996.0, 5927.0, 4966.0, 2.0, 11.0, 1.0]


...

Erreur lors du traitement du message: An error occurred while calling o113535.collectToPython
Features reçues : [24.48, 0.97, 31.5, 30.52, 12.2, 1.65, 1.2, 75.34, 11888.0, 3809.0, 11574.0, 20.0, 15.0, 2.0]


25/07/08 08:03:08 ERROR TaskSchedulerImpl: Exception in statusUpdate(0 + 4) / 4]
java.util.concurrent.RejectedExecutionException: Task org.apache.spark.scheduler.TaskResultGetter$$anon$3@6670b8ab rejected from java.util.concurrent.ThreadPoolExecutor@132f4453[Terminated, pool size = 0, active threads = 0, queued tasks = 0, completed tasks = 7091]
	at java.base/java.util.concurrent.ThreadPoolExecutor$AbortPolicy.rejectedExecution(ThreadPoolExecutor.java:2065)
	at java.base/java.util.concurrent.ThreadPoolExecutor.reject(ThreadPoolExecutor.java:833)
	at java.base/java.util.concurrent.ThreadPoolExecutor.execute(ThreadPoolExecutor.java:1365)
	at org.apache.spark.scheduler.TaskResultGetter.enqueueSuccessfulTask(TaskResultGetter.scala:61)
	at org.apache.spark.scheduler.TaskSchedulerImpl.liftedTree2$1(TaskSchedulerImpl.scala:833)
	at org.apache.spark.scheduler.TaskSchedulerImpl.statusUpdate(TaskSchedulerImpl.scala:808)
	at org.apache.spark.scheduler.local.LocalEndpoint$$anonfun$receive$1.applyO

Erreur lors du traitement du message: An error occurred while calling o113598.collectToPython.
: java.lang.IllegalStateException: SparkContext has been shutdown
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:2255)
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:2284)
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:2303)
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:2328)
	at org.apache.spark.rdd.RDD.$anonfun$collect$1(RDD.scala:1019)
	at org.apache.spark.rdd.RDDOperationScope$.withScope(RDDOperationScope.scala:151)
	at org.apache.spark.rdd.RDDOperationScope$.withScope(RDDOperationScope.scala:112)
	at org.apache.spark.rdd.RDD.withScope(RDD.scala:405)
	at org.apache.spark.rdd.RDD.collect(RDD.scala:1018)
	at org.apache.spark.sql.execution.SparkPlan.executeCollect(SparkPlan.scala:448)
	at org.apache.spark.sql.Dataset.$anonfun$collectToPython$1(Dataset.scala:3997)
	at org.apache.spark.sql.Dataset.$anonfun$withAction$2(Dataset.scala:4167)
	a

----------------------------------------
Exception occurred during processing of request from ('127.0.0.1', 39638)
ERROR:root:Exception while sending command.
Traceback (most recent call last):
  File "/home/souhail/.local/lib/python3.10/site-packages/pyspark/errors/exceptions/captured.py", line 169, in deco
    return f(*a, **kw)
  File "/home/souhail/.local/lib/python3.10/site-packages/py4j/protocol.py", line 326, in get_return_value
    raise Py4JJavaError(
py4j.protocol.Py4JJavaError: <exception str() failed>

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/home/souhail/.local/lib/python3.10/site-packages/py4j/clientserver.py", line 516, in send_command
    raise Py4JNetworkError("Answer from Java side is empty")
py4j.protocol.Py4JNetworkError: Answer from Java side is empty

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/home/souhail/.local/lib/python3

Erreur lors du traitement du message: py4j does not exist in the JVM
Features reçues : [6.42, -1.97, 35.79, 29.2, 8.96, 36.72, 0.72, 9.57, 5902.0, 4749.0, 3500.0, 4.0, 11.0, 0.0]
Erreur lors du traitement du message: [Errno 111] Connection refused
Features reçues : [40.74, 36.65, 58.75, 30.92, 13.0, 5.53, 0.59, 38.07, 6045.0, 4130.0, 8063.0, 17.0, 14.0, 1.0]
Erreur lors du traitement du message: [Errno 111] Connection refused
Features reçues : [42.07, -3.23, 24.93, 30.79, 7.08, 6.54, 4.03, 20.95, 1194.0, 10248.0, 9774.0, 10.0, 15.0, 0.0]
Erreur lors du traitement du message: [Errno 111] Connection refused
Features reçues : [23.76, 11.38, 89.23, 29.3, 6.3, 8.41, 1.62, 96.83, 8314.0, 7343.0, 3491.0, 4.0, 13.0, 0.0]
Erreur lors du traitement du message: [Errno 111] Connection refused
Features reçues : [41.91, 25.91, 57.07, 29.38, 11.3, 3.4, 0.03, 67.89, 3826.0, 1159.0, 1747.0, 15.0, 15.0, 2.0]
Erreur lors du traitement du message: [Errno 111] Connection refused
Features reçues : [33.52, -